<a href="https://colab.research.google.com/github/sibat119/papers-review-code-impl/blob/main/lda/lda_with_gensim.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## **Importing the Required Libraries**


In [1]:
!pip install pyLDAvis

In [2]:
!pip install nltk
import nltk
nltk.download("stopwords")
nltk.download('wordnet')
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
import numpy as np
import pandas as pd
import json
import glob

#Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

#vis
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis


/usr/local/lib/python3.7/dist-packages/past/types/oldstr.py:5: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated since Python 3.3,and in 3.9 it will stop working
  from collections import Iterable
/usr/local/lib/python3.7/dist-packages/sklearn/decomposition/_lda.py:29: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  EPS = np.finfo(np.float).eps


## **Load Data**

In [4]:
data = pd.read_csv("/content/Review.csv")
data.head()

Unnamed: 0  ...  Num_words_text
0           0  ...              43
1           1  ...              27
2           2  ...              53
3           3  ...              49
4           4  ...              35

[5 rows x 12 columns]

In [5]:
stopwords = stopwords.words("english")

In [6]:
print(len(stopwords), stopwords)

179 ['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than

In [7]:
reviews = pd.DataFrame(data, columns= ['Text'])
print (reviews)

                                                   Text
0     they advertise that they contain aspartame die...
1     taste disgusting having struggle just keep dow...
2     bought this zico water hoping have good taste ...
3     love terra chipswhen they bags from storei ord...
4     wanted desperately like this sauce smells tast...
...                                                 ...
9995  rescued cats female urinary infectionsshe very...
9996  love zipfizz quick energy like shakey caffeine...
9997  much except that this tastes same campbells to...
9998  after having craving mint several days went lo...
9999  office hooked these ordered assorted case from...

[10000 rows x 1 columns]


In [8]:
w_tokenizer = nltk.tokenize.WhitespaceTokenizer()
lemmatizer = nltk.stem.WordNetLemmatizer()

def lemmatize_text(text):
    return [lemmatizer.lemmatize(w) for w in w_tokenizer.tokenize(text)]

# df = pd.DataFrame(['this was cheesy', 'she likes these books', 'wow this is great'], columns=['text'])
reviews['text_lemmatized'] = reviews.Text.apply(lemmatize_text)
print(reviews)

                                                   Text                                    text_lemmatized
0     they advertise that they contain aspartame die...  [they, advertise, that, they, contain, asparta...
1     taste disgusting having struggle just keep dow...  [taste, disgusting, having, struggle, just, ke...
2     bought this zico water hoping have good taste ...  [bought, this, zico, water, hoping, have, good...
3     love terra chipswhen they bags from storei ord...  [love, terra, chipswhen, they, bag, from, stor...
4     wanted desperately like this sauce smells tast...  [wanted, desperately, like, this, sauce, smell...
...                                                 ...                                                ...
9995  rescued cats female urinary infectionsshe very...  [rescued, cat, female, urinary, infectionsshe,...
9996  love zipfizz quick energy like shakey caffeine...  [love, zipfizz, quick, energy, like, shakey, c...
9997  much except that this tastes sa

In [9]:
def gen_words(texts):
    final = []
    for text in texts:
        new = gensim.utils.simple_preprocess(text, deacc=True)
        if len(new) > 0:
          final.append(new[0])
    return(final)

data_words = gen_words(reviews)
reviews['words'] = reviews.text_lemmatized.apply(gen_words)

In [10]:
print(reviews['words'][0][:10])

['they', 'advertise', 'that', 'they', 'contain', 'aspartame', 'diet', 'flavor', 'boldly', 'state']


In [11]:
id2word = corpora.Dictionary(reviews['words'])

corpus = []
for words in reviews['words']:
  new = id2word.doc2bow(words)
  corpus.append(new)


In [12]:
print(corpus[0][:20])
word = id2word[[0][:1][0]]
print(word)

[(0, 1), (1, 1), (2, 2), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 2), (9, 1), (10, 3), (11, 1), (12, 2), (13, 1), (14, 3), (15, 1), (16, 1), (17, 1), (18, 1), (19, 2)]
advertise


In [13]:

lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=10,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.05,
                                            eta=0.05)

Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt

## **Vizualizing the Data**

In [14]:
pyLDAvis.enable_notebook()

In [15]:
# lda_viz = gensimvis.prepare(lda_model, corpus, id2word, mds="mmds", R=30)
vis_data = gensimvis.prepare(lda_model, corpus, id2word)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [16]:
pyLDAvis.display(vis_data)

In [23]:
from gensim.matutils import kullback_leibler
def get_list_of_kldiv(topics):
  kl_list = []
  i = 1
  for topic1 in topics:
    j = 1
    for topic2 in topics:
      key = str(i) + '_' + str(j)
      kl_list.append((key, kullback_leibler(topic1, topic2)))
      j += 1
    i +=1
  
  return kl_list

In [24]:
topics = lda_model.get_topics()
print(len(topics))
kldivs = get_list_of_kldiv(topics)
print(kldivs)

## **Find optimum topic count**

In [25]:

lda_5 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=5,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.05,
                                            eta=0.05)


lda_15 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.05,
                                            eta=0.05)


lda_25 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=25,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.05,
                                            eta=0.05)


lda_50 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=50,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.05,
                                            eta=0.05)

Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt

In [26]:
vis_data_5 = gensimvis.prepare(lda_5, corpus, id2word)
pyLDAvis.display(vis_data_5)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [27]:
vis_data_15 = gensimvis.prepare(lda_15, corpus, id2word)
pyLDAvis.display(vis_data_15)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [28]:
vis_data_25 = gensimvis.prepare(lda_25, corpus, id2word)
pyLDAvis.display(vis_data_25)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [29]:
vis_data_50 = gensimvis.prepare(lda_50, corpus, id2word)
pyLDAvis.display(vis_data_50)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


## **vary alpha and eta with topic number is 15**

In [30]:
lda_alpha_5 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.005,
                                            eta=0.05)

lda_alpha_10 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.10,
                                            eta=0.05)

lda_alpha_15 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.15,
                                            eta=0.05)

lda_alpha_20 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.20,
                                            eta=0.05)

lda_alpha_25 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.25,
                                            eta=0.05)

Streaming output truncated to the last 5000 lines.
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt

In [31]:
vis_data = gensimvis.prepare(lda_alpha_5, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [32]:
vis_data = gensimvis.prepare(lda_alpha_10, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [33]:
vis_data = gensimvis.prepare(lda_alpha_15, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [34]:
vis_data = gensimvis.prepare(lda_alpha_20, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [35]:
vis_data = gensimvis.prepare(lda_alpha_25, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [ ]:
lda_eta_5 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           eta=0.05,
                                           alpha=0.20)

lda_eta_10 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           eta=0.10,
                                           alpha=0.20)

lda_eta_15 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           eta=0.15,
                                           alpha=0.20)

lda_eta_20 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           eta=0.20,
                                           alpha=0.20)

lda_eta_25 = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.20,
                                            eta=0.25)

In [38]:
vis_data = gensimvis.prepare(lda_eta_5, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [39]:
vis_data = gensimvis.prepare(lda_eta_10, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [40]:
vis_data = gensimvis.prepare(lda_eta_15, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [41]:
vis_data = gensimvis.prepare(lda_eta_20, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


In [42]:
vis_data = gensimvis.prepare(lda_eta_25, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)


## **Overall best model**

In [ ]:
lda = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=id2word,
                                           num_topics=15,
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha=0.20,
                                            eta=0.05)

In [46]:
topics = lda.get_topics()
kldivs = get_list_of_kldiv(topics)
for kl in kldivs:
  print('\n', kl)


15

 ('1_1', 0.0)

 ('1_2', 6.3921804)

 ('1_3', 6.6478705)

 ('1_4', 6.619069)

 ('1_5', 6.5302873)

 ('1_6', 6.4308705)

 ('1_7', 6.440847)

 ('1_8', 6.545366)

 ('1_9', 5.8704596)

 ('1_10', 6.920045)

 ('1_11', 6.213937)

 ('1_12', 6.496245)

 ('1_13', 6.4736176)

 ('1_14', 7.6965322)

 ('1_15', 6.29594)

 ('2_1', 6.2746572)

 ('2_2', 0.0)

 ('2_3', 6.093286)

 ('2_4', 6.608193)

 ('2_5', 6.131824)

 ('2_6', 6.240517)

 ('2_7', 6.402795)

 ('2_8', 6.425856)

 ('2_9', 6.074097)

 ('2_10', 6.1266813)

 ('2_11', 6.4557543)

 ('2_12', 6.255595)

 ('2_13', 6.1677976)

 ('2_14', 6.8901086)

 ('2_15', 6.3223205)

 ('3_1', 6.6186476)

 ('3_2', 6.2628493)

 ('3_3', 0.0)

 ('3_4', 6.432473)

 ('3_5', 6.495833)

 ('3_6', 6.2022686)

 ('3_7', 6.899959)

 ('3_8', 7.0527425)

 ('3_9', 6.38203)

 ('3_10', 6.866937)

 ('3_11', 6.442297)

 ('3_12', 6.5405374)

 ('3_13', 6.3575573)

 ('3_14', 7.340553)

 ('3_15', 6.264759)

 ('4_1', 6.618296)

 ('4_2', 6.107681)

 ('4_3', 6.2736745)

 ('4_4', 0.0)



In [45]:
vis_data = gensimvis.prepare(lda, corpus, id2word)
pyLDAvis.display(vis_data)

/usr/local/lib/python3.7/dist-packages/pyLDAvis/_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  by='saliency', ascending=False).head(R).drop('saliency', 1)
